In [2]:
import math
import numpy as np
import pandas as pd
from scipy.stats import norm    # CDF = norm.cdf 
import plotly.graph_objs as go
import plotly.offline as po
import plotly.figure_factory as ff

In [ ]:
class OptionTypeError(ValueError): pass
class PositionError(ValueError): pass

In [31]:
class Options:
# AS A RULE: After creating an instance of this class (option object), don't change its attributes as an external value assignment (i.e., option_obj.s = new_spot).
# Doing so will not update the respective values of d1 and d2, and every calculation that depends on such values will be wrong.

    def __init__ (self, s, k, vol, t, r, q=0, call_or_put='call', position='long'):
        if call_or_put not in ['call','put']:
            raise OptionTypeError("Choose a valid option type between 'call' and 'put'" )
        if position not in ['long','short']:
            raise PositionError("Choose a valid position for the option between 'long' and 'short'")
        self.s = s
        self.k = k
        self.vol = vol
        self.t = t
        self.r = r
        self.q = q
        self._d1 = (math.log(s/k)+(r+(vol**2)/2)*t)/(vol*math.sqrt(t))
        self._d2 = self._d1 - vol*math.sqrt(t)
        self.call_or_put = call_or_put
        self.position = position
    
    def __eq__(self, other):
        output = (self.s == other.s) and (self.k == other.k) and (self.vol == other.vol) and (self.t == other.t) and (self.r == other.r) and (self.q == other.q) and (self.call_or_put == other.call_or_put) and (self.position == other.position) and (type(self) == type(other))
        return output
    
    def __str__(self):
        output = f"""
        European {self.call_or_put} option
        Position: {self.position}
            Spot price: {self.s}
            Strike price: {self.k}
            Implied volatility: {self.vol*100}%
            Time to maturity (years): {self.t}
            Risk-free rate: {self.r*100}%
            Dividend rate (foreign rate): {self.q*100}%

            Price: {np.round(self.bsm_valuation(), 4)}

            GREEKS
                Delta: {np.round(self.delta(), 4)}
                Gamma: {np.round(self.gamma(), 4)}
                Theta: {np.round(self.theta(), 4)} (Trading days)
                Vega: {np.round(self.vega(), 4)}
                Rho: {np.round(self.rho(), 4)}
        """
        return output

    def __repr__(self):
        output = f"Options(s={self.s}, k={self.k}, vol={self.vol}, t={self.t}, r={self.r}, q={self.q}, call_or_put='{self.call_or_put}', position='{self.position}')"
        return output
    
    @property
    def d1(self):
        return self._d1
    @property
    def d2(self):
        return self._d2

    def _n_inv(self, x):
        n = (1/math.sqrt(2*math.pi))*math.exp(-(x**2)/2)
        return n
    
    def bsm_valuation(self):
        call_price = self.s*math.exp(-self.q*self.t)*norm.cdf(self._d1) - self.k*math.exp(-self.r*self.t)*norm.cdf(self._d2)
        put_price = self.k*math.exp(-self.r*self.t)*norm.cdf(-self._d2) - self.s*math.exp(-self.q*self.t)*norm.cdf(-self._d1)
        if self.call_or_put == 'call':
            output = call_price
        elif self.call_or_put == 'put':
            output = put_price
        return output
    
    def delta(self):
        delta_call = math.exp(-self.q*self.t)*(norm.cdf(self._d1))
        delta_put = math.exp(-self.q*self.t)*(norm.cdf(self._d1)-1)
        if self.call_or_put == 'call':
            output = delta_call
        elif self.call_or_put == 'put':
            output = delta_put
        if self.position == 'short':
            output = -output
        return output
    
    def theta(self):
        theta_call = -((self.s*self._n_inv(self._d1)*self.vol*math.exp(-self.q*self.t))/(2*math.sqrt(self.t))) + self.q*self.s*norm.cdf(self._d1)*math.exp(-self.q*self.t) - self.r*self.k*math.exp(-self.r*self.t)*norm.cdf(self._d2)
        theta_put = -((self.s*self._n_inv(self._d1)*self.vol)/(2*math.sqrt(self.t))) - self.q*self.s*norm.cdf(-self._d1)*math.exp(-self.q*self.t) + self.r*self.k*math.exp(-self.r*self.t)*norm.cdf(-self._d2)
        if self.call_or_put == 'call':
            output = theta_call
        elif self.call_or_put == 'put':
            output = theta_put
        if self.position == 'short':
            output = -output
        return output

    def gamma(self):
        gamma = (self._n_inv(self._d1)*math.exp(-self.q*self.t))/(self.s*self.vol*math.sqrt(self.t))
        if self.position == 'short':
            gamma = -gamma
        return gamma

    def vega(self):
        vega = self.s*math.sqrt(self.t)*self._n_inv(self._d1)*math.exp(-self.q*self.t)
        if self.position == 'short':
            vega = -vega
        return vega

    def rho(self):
        rho_call = self.k*self.t*math.exp(-self.r*self.t)*norm.cdf(self._d2)
        rho_put = -self.k*self.t*math.exp(-self.r*self.t)*norm.cdf(-self._d2)
        if self.call_or_put == 'call':
            output = rho_call
        elif self.call_or_put == 'put':
            output = rho_put
        if self.position == 'short':
            output = -output
        return output
    
    def rho_foreign(self):
        rho_call = -self.t*math.exp(-self.q*self.t)*self.s*norm.cdf(self._d1) 
        rho_put = self.t*math.exp(-self.q*self.t)*self.s*norm.cdf(-self._d1)
        if self.call_or_put == 'call':
            output = rho_call
        elif self.call_or_put == 'put':
            output = rho_put
        if self.position == 'short':
            output = -output
        return output
    
    def greeks(self, decimals=4, foreign=False):
        if foreign==False:
            output = {
                'Delta':np.round(self.delta(), decimals),
                'Theta':np.round(self.theta(), decimals),
                'Gamma':np.round(self.gamma(), decimals),
                'Vega':np.round(self.vega(), decimals),
                'Rho':np.round(self.rho(), decimals)
            }
        else:
            output = {
                'Delta':np.round(self.delta(), decimals),
                'Theta':np.round(self.theta(), decimals),
                'Gamma':np.round(self.gamma(), decimals),
                'Vega':np.round(self.vega(), decimals),
                'Rho_domestic':np.round(self.rho(), decimals),
                'Rho_foreign':np.round(self.rho_foreign(), decimals)
            }
        return output

In [26]:
def option_strategy(list_of_options, range_width=0.3):

    # Range creation
    spot = list_of_options[0].s
    start = spot*(1-range_width)
    stop = spot*(1+range_width)
    step = (stop-start)/10000
    price_range = np.arange(start=start, stop=stop, step=step)
    
    # DataFrame to be filled
    df = pd.DataFrame(price_range).rename(columns={0:'price_range'})

    for option in list_of_options:
        
        # Parameters for payoff
        k = option.k
        price = option.bsm_valuation()
        position = option.position
        call_or_put = option.call_or_put

        # Payoff for long positions
        if (position=='long')&(call_or_put=='call'):
            payoff = [np.max([i-k,0])-price for i in price_range]
            title = 'Long Call'
        elif (position=='long')&(call_or_put=='put'):
            payoff = [np.max([k-i,0])-price for i in price_range]
            title = 'Long Put'

        # Payoff for short positions
        elif (position=='short')&(call_or_put=='call'):
            payoff = [price-np.max([i-k,0]) for i in price_range]
            title = 'Short Call'
        elif (position=='short')&(call_or_put=='put'):
            payoff = [price-np.max([k-i,0]) for i in price_range]
            title = 'Short Put'

        df[f'{title}'] = payoff
    
    df.set_index('price_range', inplace=True)
    df['Strategy'] = df.sum(axis=1)

    return df

In [27]:
def strategy_graph(df, plot_title=''):

    colors = [
        'RGB(39, 24, 126)', 
        'RGB(117, 139, 253)', 
        'RGB(174, 184, 254)',  
        'RGB(71, 181, 255)',
        'RGB(6, 40, 61)', 
        'RGB(37, 109, 133)',
    ]
    traces = []

    trace = go.Scatter(
        x = df.index,
        y = np.zeros(len(df)),
        mode = 'lines',
        name = 'Zero line',
        line = dict(width=1, dash='dash', color='black'),
        opacity=0.5
    )
    traces.append(trace)

    for x,i in enumerate(df.columns):
        
        if i == 'Strategy':
            trace = go.Scatter(
                x = df.index,
                y = df.loc[:,i],
                mode = 'lines',
                name = i,
                line = dict(width=3, color='RGB(255, 134, 0)'),
                fill='tozeroy',
                fillcolor='RGBA(255, 134, 0, 0.1)'
            )
            traces.append(trace)
        else:
            trace = go.Scatter(
                x = df.index,
                y = df.loc[:,i],
                mode = 'lines',
                name = i,
                line = dict(width=1.2, color=colors[x]),
            )
            traces.append(trace)

    layout = go.Layout(showlegend=True,
        legend={'x':1,'y':1},
        width=900,
        height=500,
        margin=dict(l=50,r=50,b=50,t=50),
        template='plotly_white',
        yaxis={'tickfont':{'size':10}, 'title':'Payoff'},
        xaxis={'tickfont':{'size':10}, 'title':'Range of Spot prices'},
        hovermode='x unified',
        title={'text':f'<b>Option Strategy</b> - {plot_title}','xanchor':'left'},
        titlefont={'size':14}
    )

    po.init_notebook_mode(connected=True)
    fig = go.Figure(data=traces, layout=layout)
    fig.update_layout(yaxis_tickprefix = '$', yaxis_tickformat = ',.2f')
    fig.update_layout(xaxis_tickprefix = '$', yaxis_tickformat = ',.2f')
    po.iplot(fig)

## Testing Zone

In [35]:
spot = 49
opt1 = Options(s=spot, k=48, vol=0.2, t=0.3846, r=0.05, call_or_put='call', position='long')
opt1.bsm_valuation()

3.454225673885915

In [17]:
print(opt1)


        European call option
        Position: long
            Spot price: 49
            Strike price: 48
            Implied volatility: 20.0%
            Time to maturity (years): 0.3846
            Risk-free rate: 5.0%
            Dividend rate (foreign rate): 0%

            Price: 3.4542

            GREEKS
                Delta: 0.6493
                Gamma: 0.061
                Theta: -4.3468 (Trading days)
                Vega: 11.2644
                Rho: 10.9069
        


In [21]:
opt1

Options(s=49, k=48, vol=0.2, t=0.3846, r=0.05, q=0, call_or_put='call', position='long')

In [27]:
opt1 = Options(s=spot, k=48, vol=0.2, t=0.3846, r=0.05, call_or_put='call', position='long')
opt2 = Options(s=spot, k=48, vol=0.2, t=0.3846, r=0.05, call_or_put='call', position='long')
opt1 == opt2

True

In [20]:
spot = 49

opt1 = Options(s=spot, k=48, vol=0.2, t=0.3846, r=0.05, call_or_put='call', position='long')
opt2 = Options(s=spot, k=50, vol=0.2, t=0.3846, r=0.05, call_or_put='put', position='long')
opt3 = Options(s=spot, k=54, vol=0.2, t=0.3846, r=0.05, call_or_put='call', position='short')
opt4 = Options(s=spot, k=50, vol=0.2, t=0.3846, r=0.05, call_or_put='put', position='short')

option_list = [opt1, 
               opt2, 
               opt3, 
               # opt4
               ]

strategy_graph(df=option_strategy(option_list), plot_title='Bull call spread')